In [1]:
import pandas as pd
!pip install shapely  # for shape in polygon function
!pip install folium==0.5.0

     |████████████████████████████████| 1.5MB 17.9MB/s eta 0:00:01


In [2]:
import json
from pandas.io.json import json_normalize

import folium 
from folium import FeatureGroup, LayerControl, Map, Marker, Popup

In [3]:
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon

point = Point(0.5, 0.5)
polygon = Polygon([(0, 0), (0, 1), (1, 1), (1, 0)])
print(polygon.contains(point))

True


In [4]:
uscensuskey="ec05fa5dc1b361505043c40ebcd446a6ace47778"

In [5]:
def revpoints(p):
    for r in pts:
        t=r[1]
        r[1]=r[0]
        r[0]=t
    return p


def getgray(value):
    b = int(max(0, 255*(1 - value)))
    g = int(max(0, 255*(1 - value)))
    r = 0 #int(max(0, 255*(1 - value)))
    hexcolour = '#%02x%02x%02x' % (r,g,b)
    return hexcolour

def addlayer(layername, layerdf, minval, maxval, themap):
    dft=layerdf[(layerdf['income100E'] > minval) & (layerdf['income100E'] <= maxval)]
    feature_group = FeatureGroup(name=layername)
    for index, row in dft.iterrows():
        pts=row['geometry.coordinates'][0]
        htmlval=f"<ul><li>{row['properties.GEOID']}</li><li>{row['income100E']}</li><li>{row['income100NE']}</li></ul>"
        folium.features.PolygonMarker(locations=pts, color='#efefef', fill_color=getgray(row['income100E']), weight=1, popup=Popup(html=htmlval)).add_to(feature_group)    
        feature_group.add_to(themap)
    return 1

In [6]:
#https://api.census.gov/data/2017/acs/acs5?get=NAME,B01001_001E&for=block%20group:*&in=state:06&in=county:111&in=tract:*
# median age at first mariage B12007_002E
#B01003_001E total pop
#B19001_001E 12 month hh income
#B19001_017E  12 month hh income +200


#df2 = pd.read_json("https://api.census.gov/data/2017/acs/acs5?get=NAME,{}&for=block%20group:*&in=state:06&in=county:111&in=tract:*&key={}".format(cenval,uscensuskey))

df2 = pd.read_json("https://api.census.gov/data/2017/acs/acs5?get=group(B19001)&for=block%20group:*&in=state:06&in=county:111&in=tract:*&key={}".format(uscensuskey))

df2sb = pd.read_json("https://api.census.gov/data/2017/acs/acs5?get=group(B19001)&for=block%20group:*&in=state:06&in=county:083&in=tract:*&key={}".format(uscensuskey))

df2 = pd.concat([
    df2,df2sb
],ignore_index=True).drop_duplicates().reset_index(drop=True)


In [7]:

df2.columns = df2.iloc[0]
df2.drop([df2.index[0]], inplace=True)

df2["geoid"] = df2["state"] + df2["county"] + df2["tract"] + df2["block group"]


In [8]:
c = df2.filter(regex='[0-9]E$',axis=1).columns
df2[c]=df2[c].astype(float)
df2["income100E"]=(df2["B19001_017E"])+(df2["B19001_016E"])
df2["income100NE"]=(df2["B19001_017E"])+(df2["B19001_016E"])

df2["income100E"]=df2["income100E"]/df2['B19001_001E']



In [9]:
df2=df2[['geoid','income100E','income100NE']]


In [10]:
!wget --quiet https://raw.githubusercontent.com/Jordan-Arthur/geojson/master/venturaandsantabarbara.json -O ventura.json
ventura_geo = r'ventura.json' # geojson file


In [11]:
dfve = pd.read_json(ventura_geo)
dfve = json_normalize(dfve['features']) 
dfve = dfve.merge(df2, left_on='properties.GEOID', right_on='geoid')

for index, row in dfve.iterrows():
    pts=row['geometry.coordinates'][0]
    p=revpoints(pts)

In [12]:
#Mapbox Bright
#Stamen Toner
#Stamen (Terrain, Toner, and Watercolor
#cartodbpositron

m = folium.Map([34.438838, -119.647062],tiles="cartodbpositron", zoom_start=10, width=1000,height=600)
l=addlayer("0 to 30", dfve, 0.0, 0.3, m)
l=addlayer("30 to 50", dfve, 0.3, 0.5, m)
l=addlayer("50 to 60", dfve, 0.5, 0.6, m)
l=addlayer("60 to 100", dfve, 0.6, 1.0, m)
folium.LayerControl( collapsed=False,).add_to(m)
m

In [13]:

#dftravel = pd.read_json("https://api.census.gov/data/2017/acs/acs5?get=group(B08303)&for=us:1&key={}".format(uscensuskey))
#dftravel = pd.read_json("https://api.census.gov/data/2017/acs/acs5?get=group(C15010)&for=block%20group:*&in=state:06&in=county:111&in=tract:*&key={}".format(uscensuskey))
df1x = pd.read_json("https://api.census.gov/data/2018/acs/acs1/variables.json")


In [14]:

c = dftravel.filter(regex='[0-9]E$',axis=1).columns
dftravel[c]=dftravel[c].astype(float)
df_t=dftravel.T


NameError: name 'dftravel' is not defined

In [ ]:


df1x1 = pd.read_json("https://api.census.gov/data/2018/acs/acs1/variables.json")
merged = pd.merge(df_t, df1x1, right_index=True, left_on=0)

merged.tail()




In [ ]:
merged.set_index('variables', inplace=True)


In [ ]:

merged.head()

#mc=merged['variables'].tolist()
#mc

#mt=merged.T

#mt.coloums=mc

#mt


In [ ]:
merged.tail(100)